In [38]:
import json
import pandas as pd
from pandas.io.json import json_normalize
import time
import os

In [39]:
#set directory
outputDir = 'output_files\\'

#combine 247 Files
two47Files = ['247_bigten.json', '247_bigtwelve.json', '247_sec.json']
main247 = []

for file in two47Files:
    conference = json.loads(open(outputDir + file, "r", encoding="utf-8").read())
    for player in conference:
        main247.append(player)

#combine rivals
rivalsFiles = ['rivals_bigten.json', 'rivals_bigtwelve.json', 'rivals_sec.json']
mainRivals = []

for file in rivalsFiles:
    conference = json.loads(open(outputDir + file, "r", encoding="utf-8").read())
    for player in conference:
        mainRivals.append(player)

#combine cfb ref
cfbRefFiles = ['cfb_ref_bigten.json', 'cfb_ref_bigtwelve.json', 'cfb_ref_sec.json']
mainCfbRef = []

for file in cfbRefFiles:
    conference = json.loads(open(outputDir + file, "r", encoding="utf-8").read())
    for player in conference:
        mainCfbRef.append(player)
                     

#Get NFL
nfl_draft_data = json.load(open('nfldraft.json'))

#All American
aaData = json.load(open('aaSelections.json'))

#combine All Conference
allConfFiles = ['SECAllConf.json', 'Ten12AllConf.json']
mainAllConf = []

for file in allConfFiles:
    conference = json.loads(open(outputDir + file, "r", encoding="utf-8").read())
    for player in conference:
        mainAllConf.append(player)

#Test Collections
two47_test = [{'school': 'maryland', 'year': '2002', '247_player': 'Randy Earle', '247_hs': 'Farmingdale Senior', '247_city': 'Farmingdale', '247_state': '1', '247_ranking': '0.9000', '247_pos': '9', '247_height': '75.0', '247_weight': '225', '247_stars': '4', '247_natl': '140'},{'school': 'maryland', 'year': '2002', '247_player': 'Andrew Thornton', '247_hs': 'Farmingdale Senior', '247_city': 'Farmingdale', '247_state': '1', '247_ranking': '0.9000', '247_pos': '9', '247_height': '75.0', '247_weight': '225', '247_stars': '4', '247_natl': '140'}]
nfl_test = [{'year': '2005', 'draft_round': '1', 'draft_pick': '12', 'team': 'SDG', 'player': 'Shawne Merriman', 'pos': 'LB', 'all_pros_first_team': '1', 'pro_bowls': '3', 'years_as_primary_starter': '4', 'g': '75', 'college_id': 'Maryland'}, {'year': '2005', 'draft_round': '1', 'draft_pick': '12', 'team': 'SDG', 'player': 'Joseph Holm', 'pos': 'LB', 'all_pros_first_team': '1', 'pro_bowls': '3', 'years_as_primary_starter': '4', 'g': '75', 'college_id': 'Maryland'}]
#rivals_test= [{'school': 'maryland', 'year': '2002', 'rivals_player': 'Jo Jo Walker', 'rivals_city': 'Carrollton', 'rivals_state': 'TX', 'rivals_hs': 'Creekview', 'rivals_pos': 'DB', 'rivals_height': 70.0, 'rivals_weight': 165.0, 'rivals_stars': 3, 'rivals_natlrk': None, 'rivals_posrk': 38, 'rivals_staterk': None}]
#Declare Field Configs
idConfigs = {'rivals' : ['playerName', 'school'], '247': ['playerName', 'school'], 'nfl' : ['player', 'college_id'], 'aa' : ['player', 'school'], 'ac' : ['playerName', 'school'], 'cr' : ['playerName', 'school']}
fieldAgg = '_'
sourceSchema = {'nfl': ['year', 'draft_round', 'draft_pick', 'team', 'pos','all_pros_first_team','pro_bowls','years_as_primary_starter','g'], 'aa' : ['year', 'afca', 'ap', 'fwaa', 'tsn', 'wcff'], 'ac' : ['year', 'coaches', 'media'], 'rivals' : ['playerName', 'city', 'state', 'highSchool', 'position', 'height', 'weight', 'stars', 'nationalRank', 'positionRank', 'stateRank'], '247' : ['playerName', 'highSchool', 'city', 'state', 'position', 'height', 'weight','nationalRank', 'positionRank', 'stateRank'], 'cr' : ['playerName', 'position', 'school', 'gamesPlayed']}

In [40]:
def createNewID (fieldList, thisDict, fieldAgg):
    finalID= ''
    for i in thisDict:
        for idx, val in enumerate(fieldList):
            if (type(i[val]) is list):
                for x in i[val]:
                    multiFinalID = []
                    multiFinalID.append(x.lower().replace(" ", "-").replace("st.", "state"))
                    #print(multiFinalID)
                i[val] = multiFinalID
                if (len(fieldList) -1 == idx):
                    finalID += i[val]
                print(multiFinalID)
                i['ID'] = multiFinalID
            elif (type(val) is not list):
                i[val] = i[val].lower().replace(" ", "-").replace("st.", "state")
                #print(fieldList[idx])
                if (len(fieldList) - 1 == idx):
                    finalID += i[val]
                else:
                    finalID += i[val] + fieldAgg
                i['ID'] = finalID
        i['ID'] = finalID
        finalID=''

#TEST CASES
#for i in two47_test:
#    createNewID(idConfigs['247'], two47_test, fieldAgg)
#print(two47_test)


In [41]:
def comparator (field1, field2):
    areTheyEqual = False
    if field2 is not list:
        if equals(field1, field2):
            areTheyEqual =True
    elif field2 is list:
        for x in field2:
            if (field1 == x):
                areTheyEqual = True
    return areTheyEqual

In [42]:
#function to join to nfl draft
def joinData (masterDict, secondDict, schema):
    for player in masterDict:
        for record in secondDict:
            if (comparator(player['ID'],record['ID'])):
                player[schema] = {}
                for x in sourceSchema[schema]:
                    try:
                        player[schema][x] = record[x]
                    except KeyError:
                        print(player['id'])
                break;


In [43]:
def equals(first, second):
    # Return true if the two ints are equal.
    return first == second

In [44]:
createNewID(idConfigs['247'], main247, fieldAgg)
createNewID(idConfigs['rivals'], mainRivals, fieldAgg)
createNewID(idConfigs['nfl'], nfl_draft_data, fieldAgg)
createNewID(idConfigs['aa'], aaData, fieldAgg)
createNewID(idConfigs['ac'], mainAllConf, fieldAgg)

In [45]:
#print(mainCfbRef)
createNewID(idConfigs['cr'], mainCfbRef, fieldAgg)
print(mainCfbRef)

['illinois']
['illinois']
['illinois']
['illinois']
['illinois']
['illinois']
['illinois']
['virginiatech']
['illinois']
['illinois']
['illinois']
['illinois']
['illinois']
['illinois']
['illinois']
['illinois']
['illinois']
['illinois']
['illinois']
['illinois']
['illinois']
['illinois']
['illinois']
['illinois']
['illinois']
['illinois']
['illinois']
['illinois']
['illinois']
['illinois']
['illinois']
['illinois']
['illinois']
['illinois']
['illinois']
['illinois']
['illinois']
['illinois']
['illinois']
['illinois']
['illinois']
['illinois']
['illinois']
['illinois']
['illinois']
['illinois']
['illinois']
['illinois']
['illinois']
['illinois']
['illinois']
['illinois']
['illinois']
['illinois']
['illinois']
['illinois']
['illinois']
['illinois']
['illinois']
['illinois']
['illinois']
['illinois']
['illinois']
['illinois']
['illinois']
['illinois']
['illinois']
['illinois']
['illinois']
['illinois']
['illinois']
['illinois']
['illinois']
['illinois']
['illinois']
['illinois']
['illino

['maryland']
['maryland']
['maryland']
['maryland']
['maryland']
['maryland']
['maryland']
['maryland']
['maryland']
['maryland']
['maryland']
['maryland']
['maryland']
['maryland']
['maryland']
['maryland']
['maryland']
['maryland']
['maryland']
['maryland']
['maryland']
['maryland']
['maryland']
['maryland']
['maryland']
['maryland']
['maryland']
['maryland']
['maryland']
['maryland']
['maryland']
['maryland']
['maryland']
['maryland']
['maryland']
['maryland']
['maryland']
['maryland']
['maryland']
['maryland']
['maryland']
['maryland']
['maryland']
['maryland']
['maryland']
['maryland']
['maryland']
['maryland']
['maryland']
['maryland']
['maryland']
['maryland']
['maryland']
['maryland']
['maryland']
['maryland']
['maryland']
['maryland']
['maryland']
['maryland']
['maryland']
['maryland']
['maryland']
['maryland']
['maryland']
['maryland']
['maryland']
['maryland']
['maryland']
['maryland']
['maryland']
['maryland']
['maryland']
['maryland']
['maryland']
['maryland']
['maryland']

['minnesota']
['minnesota']
['minnesota']
['minnesota']
['minnesota']
['minnesota']
['minnesota']
['minnesota']
['minnesota']
['minnesota']
['minnesota']
['minnesota']
['minnesota']
['minnesota']
['minnesota']
['minnesota']
['minnesota']
['minnesota']
['minnesota']
['minnesota']
['minnesota']
['minnesota']
['minnesota']
['minnesota']
['minnesota']
['minnesota']
['minnesota']
['minnesota']
['minnesota']
['minnesota']
['minnesota']
['minnesota']
['minnesota']
['minnesota']
['minnesota']
['minnesota']
['minnesota']
['minnesota']
['minnesota']
['minnesota']
['minnesota']
['minnesota']
['minnesota']
['minnesota']
['minnesota']
['minnesota']
['minnesota']
['minnesota']
['minnesota']
['minnesota']
['minnesota']
['minnesota']
['minnesota']
['minnesota']
['minnesota']
['minnesota']
['minnesota']
['minnesota']
['minnesota']
['minnesota']
['minnesota']
['minnesota']
['minnesota']
['minnesota']
['minnesota']
['minnesota']
['minnesota']
['minnesota']
['minnesota']
['minnesota']
['minnesota']
['minn

['pennstate']
['pennstate']
['pennstate']
['pennstate']
['pennstate']
['pennstate']
['pennstate']
['pennstate']
['pennstate']
['pennstate']
['pennstate']
['pennstate']
['pennstate']
['pennstate']
['pennstate']
['pennstate']
['pennstate']
['pennstate']
['pennstate']
['pennstate']
['pennstate']
['pennstate']
['pennstate']
['pennstate']
['pennstate']
['pennstate']
['pennstate']
['pennstate']
['pennstate']
['pennstate']
['pennstate']
['pennstate']
['pennstate']
['pennstate']
['pennstate']
['pennstate']
['pennstate']
['pennstate']
['pennstate']
['pennstate']
['pennstate']
['pennstate']
['pennstate']
['pennstate']
['pennstate']
['pennstate']
['pennstate']
['pennstate']
['pennstate']
['pennstate']
['pennstate']
['pennstate']
['pennstate']
['pennstate']
['pennstate']
['pennstate']
['pennstate']
['pennstate']
['pennstate']
['pennstate']
['pennstate']
['pennstate']
['pennstate']
['pennstate']
['pennstate']
['pennstate']
['pennstate']
['pennstate']
['pennstate']
['pennstate']
['pennstate']
['penn

['rutgers']
['rutgers']
['rutgers']
['rutgers']
['rutgers']
['rutgers']
['rutgers']
['rutgers']
['rutgers']
['rutgers']
['rutgers']
['rutgers']
['rutgers']
['rutgers']
['rutgers']
['rutgers']
['rutgers']
['rutgers']
['rutgers']
['rutgers']
['rutgers']
['rutgers']
['rutgers']
['rutgers']
['rutgers']
['rutgers']
['rutgers']
['rutgers']
['rutgers']
['rutgers']
['rutgers']
['rutgers']
['rutgers']
['rutgers']
['rutgers']
['rutgers']
['rutgers']
['rutgers']
['rutgers']
['rutgers']
['rutgers']
['rutgers']
['rutgers']
['rutgers']
['rutgers']
['rutgers']
['rutgers']
['rutgers']
['rutgers']
['rutgers']
['rutgers']
['rutgers']
['rutgers']
['rutgers']
['rutgers']
['rutgers']
['rutgers']
['rutgers']
['rutgers']
['rutgers']
['rutgers']
['rutgers']
['rutgers']
['rutgers']
['rutgers']
['rutgers']
['rutgers']
['rutgers']
['rutgers']
['virginiatech']
['rutgers']
['rutgers']
['rutgers']
['rutgers']
['rutgers']
['rutgers']
['rutgers']
['rutgers']
['rutgers']
['rutgers']
['rutgers']
['rutgers']
['rutgers']

...

['arkansas']
['arkansas']
['arkansas']
['arkansas']
['arkansas']
['arkansas']
['arkansas']
['arkansas']
['arkansas']
['arkansas']
['arkansas']
['arkansas']
['arkansas']
['arkansas']
['arkansas']
['arkansas']
['arkansas']
['arkansas']
['arkansas']
['arkansas']
['arkansas']
['arkansas']
['arkansas']
['arkansas']
['arkansas']
['arkansas']
['arkansas']
['arkansas']
['arkansas']
['arkansas']
['arkansas']
['arkansas']
['arkansas']
['arkansas']
['arkansas']
['arkansas']
['arkansas']
['arkansas']
['arkansas']
['arkansas']
['arkansas']
['arkansas']
['arkansas']
['arkansas']
['arkansas']
['arkansas']
['arkansas']
['arkansas']
['arkansas']
['arkansas']
['arkansas']
['arkansas']
['arkansas']
['arkansas']
['arkansas']
['arkansas']
['arkansas']
['arkansas']
['arkansas']
['arkansas']
['arkansas']
['arkansas']
['arkansas']
['arkansas']
['arkansas']
['arkansas']
['arkansas']
['arkansas']
['arkansas']
['arkansas']
['arkansas']
['arkansas']
['arkansas']
['arkansas']
['arkansas']
['arkansas']
['arkansas']

['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['georgia']
['ge

['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['olemiss']
['ol

['tennessee']
['tennessee']
['tennessee']
['tennessee']
['tennessee']
['tennessee']
['tennessee']
['tennessee']
['tennessee']
['tennessee']
['tennessee']
['tennessee']
['tennessee']
['tennessee']
['tennessee']
['tennessee']
['tennessee']
['tennessee']
['tennessee']
['tennessee']
['tennessee']
['tennessee']
['tennessee']
['tennessee']
['tennessee']
['tennessee']
['tennessee']
['tennessee']
['tennessee']
['tennessee']
['tennessee']
['tennessee']
['tennessee']
['tennessee']
['tennessee']
['tennessee']
['tennessee']
['tennessee']
['tennessee']
['tennessee']
['tennessee']
['tennessee']
['tennessee']
['tennessee']
['tennessee']
['tennessee']
['tennessee']
['tennessee']
['tennessee']
['tennessee']
['tennessee']
['tennessee']
['tennessee']
['tennessee']
['tennessee']
['tennessee']
['tennessee']
['tennessee']
['tennessee']
['tennessee']
['tennessee']
['tennessee']
['tennessee']
['tennessee']
['tennessee']
['tennessee']
['tennessee']
['tennessee']
['tennessee']
['tennessee']
['tennessee']
['tenn

['vanderbilt']
['vanderbilt']
['vanderbilt']
['vanderbilt']
['vanderbilt']
['vanderbilt']
['vanderbilt']
['vanderbilt']
['vanderbilt']
['vanderbilt']
['vanderbilt']
['vanderbilt']
['vanderbilt']
['vanderbilt']
['vanderbilt']
['vanderbilt']
['vanderbilt']
['vanderbilt']
['vanderbilt']
['vanderbilt']
['vanderbilt']
['vanderbilt']
['vanderbilt']
['vanderbilt']
['vanderbilt']
['vanderbilt']
['vanderbilt']
['vanderbilt']
['vanderbilt']
['vanderbilt']
['vanderbilt']
['vanderbilt']
['vanderbilt']
['vanderbilt']
['vanderbilt']
['vanderbilt']
['vanderbilt']
['vanderbilt']
['vanderbilt']
['vanderbilt']
['vanderbilt']
['vanderbilt']
['vanderbilt']
['vanderbilt']
['vanderbilt']
['vanderbilt']
['vanderbilt']
['vanderbilt']
['vanderbilt']
['vanderbilt']
['vanderbilt']
['vanderbilt']
['vanderbilt']
['vanderbilt']
['vanderbilt']
['vanderbilt']
['vanderbilt']
['vanderbilt']
['vanderbilt']
['vanderbilt']
['vanderbilt']
['vanderbilt']
['vanderbilt']
['vanderbilt']
['vanderbilt']
['vanderbilt']
['vanderbi

In [54]:
# This creates the root of each recruit in the JSON.  Anything that can be pulled out from the various sources is here
masterData = []
for recruit in main247:
    masterRecruit = {}
    masterRecruit['ID'] = recruit['ID']
    masterRecruit['year'] = recruit['year']
    masterRecruit['school'] = recruit['school']
    masterRecruit['compositeScore'] = recruit['compRating']
    masterRecruit['compositeStars'] = recruit['compStars']
    masterData.append(masterRecruit)

In [55]:
joinData(masterData, main247, '247')
joinData(masterData,mainRivals, 'rivals')
joinData(masterData,nfl_draft_data,  'nfl')
joinData(masterData, aaData,  'aa')
joinData(masterData, mainAllConf, 'ac')
joinData(masterData, mainCfbRef, 'cr')


In [56]:
with open("final_output.json", "w") as write_file:
    json.dump(masterData, write_file)

In [ ]:
## NOTE: Bag of Words depends on strings being converted to floats for comparison.  So none of this works.  Pivoting to the levensthein Distance

from sklearn.tree import DecisionTreeClassifier
from sklearn.neighbors import KNeighborsClassifier
from sklearn.neural_network import MLPClassifier
from sklearn.ensemble import RandomForestClassifier

X = [['stefondiggs_maryland', 'stefondiggs_maryland'],['kjhamler_pennstate', 'kjhamler_pennst.'],['trevondiggs_alabama', 'trevondiggs_alabama'],['alexsmith_utah', 'alexsmith_texas'],['kellenmonde_texasam', 'kellenmond_texasa&m']]
Y = ['true','true','true','false','true']

P = [['djmoore_maryland', 'djmoore_maryland'], ['colinkapernick_utahstate', 'collinkapernick_utahst']]

c = DecisionTreeClassifier()
c = c.fit(X,Y)
print("Prediction: " + str(c.predict(P)))

knn = KNeighborsClassifier()
knn.fit(X,Y)
print ("2 Using K Neighbors Classifier Prediction is " + str(knn.predict(P)))

mlpc = MLPClassifier()
mlpc.fit(X,Y)
print ("3) Using MLPC Classifier Prediction is " + str(mlpc.predict(P)))

rfor = RandomForestClassifier()
rfor.fit(X,Y)
print ("4) Using RandomForestClassifier Prediction is " + str(rfor.predict(P)))

In [104]:
print(json.loads(open("output_files\\247_bigten.json", "r", encoding="utf-8").read()))

[{'school': 'illinois', 'year': '2002', 'playerName': 'James McGill', 'highSchool': 'Bakersfield College', 'city': 'Bakersfield', 'state': 'CA', 'compRating': '0.9333', 'position': 'S', 'height': 74.0, 'weight': '215', 'compStars': 4, 'nationalRank': '22', 'positionRank': '2', 'stateRank': '9'}, {'school': 'illinois', 'year': '2002', 'playerName': 'Ibrahim Halsey', 'highSchool': 'Elizabeth', 'city': 'Elizabeth', 'state': 'NJ', 'compRating': '0.8667', 'position': 'RB', 'height': 71.0, 'weight': '190', 'compStars': 3, 'nationalRank': '306', 'positionRank': '24', 'stateRank': '6'}, {'school': 'illinois', 'year': '2002', 'playerName': 'Cyruss Garrett', 'highSchool': 'Romeoville', 'city': 'Romeoville', 'state': 'IL', 'compRating': '0.8667', 'position': 'OLB', 'height': 75.0, 'weight': '220', 'compStars': 3, 'nationalRank': '348', 'positionRank': '19', 'stateRank': '6'}, {'school': 'illinois', 'year': '2002', 'playerName': 'Mel Bryant', 'highSchool': 'Muncie Central', 'city': 'Muncie', 'stat